In [1]:
import os
import sys
print("Current Dir:", os.getcwd())
sys.path.append(os.getcwd())
print("sys.path =", sys.path)


Current Dir: /home/user/dev_ws/src/diffusion-model-for-arm-public
sys.path = ['/usr/lib/python310.zip', '/usr/lib/python3.10', '/usr/lib/python3.10/lib-dynload', '', '/home/user/.local/lib/python3.10/site-packages', '/usr/local/lib/python3.10/dist-packages', '/usr/lib/python3/dist-packages', '/home/user/dev_ws/src/diffusion-model-for-arm-public']


In [2]:
from simulator import definition as armdef
print(armdef)  # 成功すれば <module 'simulator.definition' from ...> が出る


<module 'simulator.definition' from '/home/user/dev_ws/src/diffusion-model-for-arm-public/simulator/definition.py'>


In [3]:
from diffusion_model.model import Dataset


In [4]:
import os
import pandas as pd
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, random_split
from tqdm import tqdm_notebook as tqdm
!pip install pygame
import sys
import os

# diffusion_model-for-arm-public を sys.path に追加
# sys.path.append(os.path.abspath("."))  # 現在位置が diffusion-model-for-arm-public ならこれでOK
# または
sys.path.append(os.path.abspath("./diffusion_model"))  # model.pyから見て正しいならこちら

# モジュールが読み込めるか確認
from simulator import definition as armdef


Defaulting to user installation because normal site-packages is not writeable


In [5]:
import sys
!{sys.executable} -m pip install pygame

from diffusion_model import Dataset, EarlyStopping, Model, gen_xt, normalize, steps

Defaulting to user installation because normal site-packages is not writeable


In [6]:
# Notebookの先頭でこれを実行
import sys
import os
sys.path.append(os.path.abspath("."))  # diffusion-model-for-arm-public を含む

# 確認：これでmodel.pyをimportできるようになるはず
from diffusion_model import Dataset, EarlyStopping, Model, gen_xt, normalize, steps


In [7]:
import sys
print(sys.path)


['/usr/lib/python310.zip', '/usr/lib/python3.10', '/usr/lib/python3.10/lib-dynload', '', '/home/user/.local/lib/python3.10/site-packages', '/usr/local/lib/python3.10/dist-packages', '/usr/lib/python3/dist-packages', '/home/user/dev_ws/src/diffusion-model-for-arm-public', '/home/user/dev_ws/src/diffusion-model-for-arm-public/diffusion_model', '/home/user/dev_ws/src/diffusion-model-for-arm-public']


In [8]:
# 例（venv使用時）
!python3 -mpip install ipykernel
!python3 -m ipykernel install --user --name myenv --display-name "Python (myenv)"


Defaulting to user installation because normal site-packages is not writeable
Installed kernelspec myenv in /home/user/.local/share/jupyter/kernels/myenv


In [9]:
import torch
print(torch.__version__)
print(torch.version.cuda)  # None ならCPU版


2.6.0+cu124
12.4


In [10]:
# PyTorch CUDA対応版をインストール（例: CUDA 11.8対応のPyTorch）
!pip install torch torchvision torchaudio --index-url https://download.pytorch.org/whl/cu118


Defaulting to user installation because normal site-packages is not writeable
Looking in indexes: https://download.pytorch.org/whl/cu118


In [11]:
from tqdm import tqdm
import torch
import torch.nn as nn
from torch.utils.data import DataLoader, random_split

In [12]:
#データセットの読み込み
device = "cuda"
dataset = Dataset("data/train.csv")
model = Model(steps).to(device)

In [13]:
batch_size = 100
# データローダーの初期化
dataloader = torch.utils.data.DataLoader(
        dataset,
        batch_size=batch_size,
        shuffle=True,
        num_workers=14,
        drop_last=True,
        pin_memory=True,
    )
train_size = int(len(dataset) * 0.8)
val_size = len(dataset) - train_size
train_dataset, val_dataset = random_split(
        dataset, [train_size, val_size], generator=torch.Generator().manual_seed(42)
    )

train_dataloader = DataLoader(
        train_dataset,
        batch_size=batch_size,
        shuffle=True,
    )
val_dataloader = DataLoader(
        val_dataset,
        batch_size=batch_size,
        shuffle=False,
    )

In [14]:
epochs = 20
optimizer = torch.optim.Adam(model.parameters(), lr=0.001, weight_decay=0.001)
scheduler = torch.optim.lr_scheduler.LinearLR(
        optimizer,
        start_factor=1,
        end_factor=0.1,
        total_iters=epochs,
    )
criterion = nn.MSELoss()
# EarlyStoppingクラスを使用して、学習の早期終了を設定
early_stopping = EarlyStopping(
        # patienceを5に設定
        patience=5,
        # min_deltaを0.001に設定
        delta=0.01,
    )

In [ ]:
# 学習を開始
for epoch in tqdm(range(epochs)):
    model.train()
    total_loss = 0
    # 各バッチを(x, pos, theta)という形式のタプルとして取得し、enumerateメソッドを使用してデータローダーからバッチを順番に取得し、各バッチに対してインデックスを付ける。
    for batch, (x, pos, theta) in enumerate(dataloader):
        # データをGPUに転送
        x, pos, theta = x.to(device), pos.to(device), theta.to(device)
        # xを正規化
        x = normalize(x)
        print(x)
        # torch.randintメソッドを使用して、1からsteps(25)までの値をランダムに生成し、バッチサイズ（100）行1列のテンソルを生成
        t = torch.randint(1, steps, (batch_size,), device=device).long()
        # torch.randn_likeメソッドを使用して、正規分布に従うランダムな値を持つxと同じサイズのテンソルを生成
        y = torch.randn_like(x).to(device)
        # gen_xtメソッド(ノイズを生成）を使用して、x, t, yを引数として渡し、xを生成
        x = gen_xt(x, t, y)
        # x及びyをデバイスに転送
        x, y = x.to(device), y.to(device)
        # モデルにx, t, posを引数として渡し、予測値を取得
        pred = model(x, t, pos)
        # 平均二乗誤差損失関数を使用して、予測値とyの損失を計算
        loss = criterion(pred, y)
        # 勾配を初期化
        optimizer.zero_grad()
        # 逆伝播を実行
        loss.backward()
        # 学習率と最適化手法に基づいて、パラメータを更新
        optimizer.step()
        # epoch全体の損失を、各バッチの損失を累積することによって計算
        total_loss += loss.item()
    print(f"Epoch {epoch}: train_loss = {total_loss / len(dataloader):.4f}")
    scheduler.step()
    # 検証
    model.eval()
    val_loss = 0.0
    with torch.no_grad():
        for x_val, pos_val, theta_val in val_dataloader:
            x_val, pos_val, theta_val = (
                    x_val.to(device),
                    pos_val.to(device),
                    theta_val.to(device),
                )
            x_val = normalize(x_val)
            t_val = torch.randint(1, steps, (x_val.size(0),), device=device).long()
            y_val = torch.randn_like(x_val).to(device)
            x_val = gen_xt(x_val, t_val, y_val)

            pred_val = model(x_val, t_val, pos_val)
            loss_val = criterion(pred_val, y_val)
            val_loss += loss_val.item()
        val_loss /= len(val_dataloader)

  0% 0/20 [00:00<?, ?it/s]
0it [00:00, ?it/s]
1it [00:00,  7.21it/s]
42it [00:00, 209.58it/s]
83it [00:00, 290.62it/s]
119it [00:00, 316.15it/s]
163it [00:00, 357.08it/s]
208it [00:00, 387.46it/s]
254it [00:00, 409.89it/s]
299it [00:00, 422.28it/s]
345it [00:00, 432.11it/s]
391it [00:01, 439.82it/s]
437it [00:01, 443.83it/s]
483it [00:01, 448.00it/s]
529it [00:01, 450.79it/s]
575it [00:01, 451.08it/s]
621it [00:01, 450.27it/s]
667it [00:01, 451.72it/s]
713it [00:01, 452.63it/s]
759it [00:01, 453.48it/s]
805it [00:01, 454.33it/s]
851it [00:02, 454.90it/s]
897it [00:02, 455.18it/s]
943it [00:02, 456.28it/s]
989it [00:02, 457.36it/s]
1035it [00:02, 454.13it/s]
1082it [00:02, 456.16it/s]
1129it [00:02, 457.38it/s]
1175it [00:02, 457.41it/s]
1222it [00:02, 458.32it/s]
1269it [00:02, 459.11it/s]
1316it [00:03, 459.49it/s]
1363it [00:03, 460.52it/s]
1410it [00:03, 460.81it/s]
1457it [00:03, 461.10it/s]
1504it [00:03, 461.72it/s]
1551it [00:03, 461.77it/s]
1598it [00:03, 461.87it/s]
1645it [00

Epoch 0: train_loss = 1.0005


  5% 1/20 [04:25<1:24:03, 265.45s/it]
0it [00:00, ?it/s]
34it [00:00, 338.86it/s]
74it [00:00, 371.63it/s]
113it [00:00, 379.10it/s]
155it [00:00, 391.96it/s]
197it [00:00, 399.86it/s]
241it [00:00, 412.40it/s]
283it [00:00, 409.27it/s]
328it [00:00, 420.62it/s]
374it [00:00, 432.78it/s]
420it [00:01, 439.92it/s]
466it [00:01, 445.69it/s]
512it [00:01, 449.67it/s]
558it [00:01, 452.31it/s]
604it [00:01, 453.19it/s]
650it [00:01, 454.51it/s]
696it [00:01, 455.60it/s]
742it [00:01, 456.81it/s]
788it [00:01, 456.29it/s]
834it [00:01, 456.80it/s]
880it [00:02, 457.13it/s]
926it [00:02, 456.41it/s]
972it [00:02, 454.68it/s]
1018it [00:02, 453.27it/s]
1064it [00:02, 451.89it/s]
1110it [00:02, 450.68it/s]
1156it [00:02, 448.39it/s]
1201it [00:02, 432.52it/s]
1245it [00:02, 400.44it/s]
1290it [00:02, 413.30it/s]
1335it [00:03, 423.25it/s]
1381it [00:03, 431.24it/s]
1427it [00:03, 437.53it/s]
1473it [00:03, 441.41it/s]
1518it [00:03, 442.44it/s]
1564it [00:03, 445.77it/s]
1610it [00:03, 447.90i

Epoch 1: train_loss = 1.0002


 10% 2/20 [08:56<1:20:37, 268.78s/it]
0it [00:00, ?it/s]
15it [00:00, 149.32it/s]
48it [00:00, 252.18it/s]
81it [00:00, 284.49it/s]
126it [00:00, 347.00it/s]
172it [00:00, 386.10it/s]
218it [00:00, 408.61it/s]
264it [00:00, 424.26it/s]
307it [00:00, 423.71it/s]
350it [00:00, 420.76it/s]
396it [00:01, 432.20it/s]
443it [00:01, 440.70it/s]
489it [00:01, 446.46it/s]
535it [00:01, 448.86it/s]
581it [00:01, 449.07it/s]
626it [00:01, 421.59it/s]
669it [00:01, 417.53it/s]
714it [00:01, 424.42it/s]
760it [00:01, 433.31it/s]
806it [00:01, 439.22it/s]
852it [00:02, 442.89it/s]
898it [00:02, 446.11it/s]
944it [00:02, 447.50it/s]
989it [00:02, 444.47it/s]
1034it [00:02, 445.15it/s]
1079it [00:02, 444.96it/s]
1124it [00:02, 445.59it/s]
1169it [00:02, 446.77it/s]
1214it [00:02, 444.21it/s]
1259it [00:02, 438.62it/s]
1303it [00:03, 438.16it/s]
1347it [00:03, 433.18it/s]
1391it [00:03, 434.79it/s]
1436it [00:03, 439.21it/s]
1481it [00:03, 441.91it/s]
1526it [00:03, 444.17it/s]
1571it [00:03, 445.75it/

...

 75% 15/20 [4:47:54<1:55:25, 1385.00s/it]
0it [00:00, ?it/s]
7it [00:00, 64.28it/s]
16it [00:00, 72.63it/s]
25it [00:00, 78.80it/s]
33it [00:00, 76.87it/s]
42it [00:00, 79.90it/s]
51it [00:00, 78.37it/s]
60it [00:00, 79.22it/s]
70it [00:00, 83.29it/s]
79it [00:00, 83.64it/s]
88it [00:01, 81.50it/s]
97it [00:01, 75.87it/s]
105it [00:01, 76.23it/s]
116it [00:01, 84.34it/s]
125it [00:01, 83.97it/s]
134it [00:01, 80.37it/s]
143it [00:01, 81.46it/s]
152it [00:01, 83.66it/s]
162it [00:01, 86.53it/s]
171it [00:02, 86.84it/s]
180it [00:02, 85.81it/s]
189it [00:02, 82.18it/s]
198it [00:02, 82.96it/s]
208it [00:02, 87.05it/s]
219it [00:02, 91.83it/s]
229it [00:02, 87.57it/s]
238it [00:02, 85.77it/s]
247it [00:02, 83.81it/s]
256it [00:03, 81.66it/s]
265it [00:03, 76.73it/s]
273it [00:03, 73.45it/s]
282it [00:03, 77.40it/s]
290it [00:03, 76.61it/s]
299it [00:03, 79.25it/s]
309it [00:03, 84.08it/s]
318it [00:03, 84.53it/s]
327it [00:04, 81.72it/s]
336it [00:04, 81.05it/s]
345it [00:04, 82.15it/s]
3

Epoch 15: train_loss = 0.9997


 80% 16/20 [5:11:07<1:32:30, 1387.60s/it]
0it [00:00, ?it/s]
6it [00:00, 53.98it/s]
14it [00:00, 66.18it/s]
23it [00:00, 74.77it/s]
32it [00:00, 79.59it/s]
43it [00:00, 86.23it/s]
52it [00:00, 86.03it/s]
62it [00:00, 86.65it/s]
72it [00:00, 89.07it/s]
82it [00:00, 91.69it/s]
92it [00:01, 85.89it/s]
102it [00:01, 87.16it/s]
111it [00:01, 87.27it/s]
120it [00:01, 84.12it/s]
129it [00:01, 76.37it/s]
138it [00:01, 78.98it/s]
148it [00:01, 83.04it/s]
157it [00:01, 83.67it/s]
166it [00:01, 84.71it/s]
175it [00:02, 84.32it/s]
185it [00:02, 87.71it/s]
194it [00:02, 84.15it/s]
203it [00:02, 81.36it/s]
212it [00:02, 83.63it/s]
221it [00:02, 83.60it/s]
230it [00:02, 78.66it/s]
238it [00:02, 77.16it/s]
246it [00:03, 75.56it/s]
254it [00:03, 73.04it/s]
262it [00:03, 74.76it/s]
270it [00:03, 69.85it/s]
278it [00:03, 69.86it/s]
286it [00:03, 70.12it/s]
294it [00:03, 71.95it/s]
304it [00:03, 77.67it/s]
313it [00:03, 80.77it/s]
322it [00:04, 82.25it/s]
331it [00:04, 82.37it/s]
340it [00:04, 81.94it/s]


Epoch 16: train_loss = 1.0000


 85% 17/20 [5:34:23<1:09:29, 1389.85s/it]
0it [00:00, ?it/s]
7it [00:00, 61.50it/s]
15it [00:00, 71.63it/s]
25it [00:00, 81.01it/s]
34it [00:00, 81.76it/s]
43it [00:00, 79.07it/s]
51it [00:00, 78.57it/s]
60it [00:00, 78.83it/s]
68it [00:00, 74.77it/s]
77it [00:00, 76.88it/s]
85it [00:01, 77.08it/s]
94it [00:01, 79.85it/s]
103it [00:01, 80.04it/s]
113it [00:01, 85.51it/s]
122it [00:01, 82.07it/s]
131it [00:01, 80.13it/s]
140it [00:01, 77.88it/s]
148it [00:01, 76.36it/s]
156it [00:02, 72.53it/s]
164it [00:02, 73.77it/s]
172it [00:02, 74.96it/s]
181it [00:02, 77.09it/s]
189it [00:02, 76.63it/s]
199it [00:02, 82.01it/s]
211it [00:02, 92.44it/s]
221it [00:02, 86.97it/s]
230it [00:02, 86.05it/s]
239it [00:02, 84.35it/s]
248it [00:03, 82.87it/s]
257it [00:03, 83.36it/s]
266it [00:03, 81.79it/s]
275it [00:03, 80.33it/s]
284it [00:03, 81.61it/s]
293it [00:03, 80.79it/s]
303it [00:03, 84.60it/s]
313it [00:03, 87.84it/s]
323it [00:03, 90.21it/s]
333it [00:04, 89.75it/s]
342it [00:04, 88.40it/s]
3